In [ ]:
# get MetaMarkers

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(dplyr)
library(MetaMarkers)

In [3]:
# 'data' has cpm-normalized values
sc1 = readRDS('Govek_A1N1N2.rds')
sc1

An object of class Seurat 
61021 features across 26612 samples within 1 assay 
Active assay: RNA (61021 features, 0 variable features)
 2 layers present: counts, data

In [4]:
# get CPM exp mat
exp1 = LayerData(sc1, assay = 'RNA', layer = 'data') # cpm

In [5]:
table(sc1$celltype_N1N2)


 double_positive Neurog1_positive Neurog2_positive             none 
             855              257            16354             9146 

In [13]:
sc1@meta.data[1:2,]

orig.ident    nCount_RNA nFeature_RNA
AAACCCAAGGCTCCCA_1_1_1_1 SeuratProject 4098       2156        
AAACCCAAGTATAGGT_1_1_1_1 SeuratProject 4261       2111        
                         organism_ontology_term_id tissue_ontology_term_id
AAACCCAAGGCTCCCA_1_1_1_1 NCBITaxon:10090           UBERON:0001894         
AAACCCAAGTATAGGT_1_1_1_1 NCBITaxon:10090           UBERON:0001894         
                         assay_ontology_term_id disease_ontology_term_id
AAACCCAAGGCTCCCA_1_1_1_1 EFO:0009922            PATO:0000461            
AAACCCAAGTATAGGT_1_1_1_1 EFO:0009922            PATO:0000461            
                         cell_type_ontology_term_id
AAACCCAAGGCTCCCA_1_1_1_1 CL:0000679                
AAACCCAAGTATAGGT_1_1_1_1 CL:0000617                
                         self_reported_ethnicity_ontology_term_id
AAACCCAAGGCTCCCA_1_1_1_1 na                                      
AAACCCAAGTATAGGT_1_1_1_1 na                                      
                         development_stage_ontology_term_id ⋯ assay     disease
AAACCCAAGGCTCCCA_1_1_1_1 MmusDv:0000027                     ⋯ 10x 3' v3 normal 
AAACCCAAGTATAGGT_1_1_1_1 MmusDv:0000027                     ⋯ 10x 3' v3 normal 
                         organism     sex    tissue      
AAACCCAAGGCTCCCA_1_1_1_1 Mus musculus female diencephalon
AAACCCAAGTATAGGT_1_1_1_1 Mus musculus female diencephalon
                         self_reported_ethnicity development_stage
AAACCCAAGGCTCCCA_1_1_1_1 na                      Theiler stage 20 
AAACCCAAGTATAGGT_1_1_1_1 na                      Theiler stage 20 
                         observation_joinid celltype_A1N2    celltype_N1N2   
AAACCCAAGGCTCCCA_1_1_1_1 <I>iccIqCO         Neurog2_positive Neurog2_positive
AAACCCAAGTATAGGT_1_1_1_1 0bu^zDIoAJ         Neurog2_positive double_positive

In [18]:
# get SCE object
keepids = which(sc1$celltype_N1N2!='none')
names(keepids) = NULL
sce2 = SingleCellExperiment(list(cpm = LayerData(sc1, assay = 'RNA', layer = 'data')[,keepids]))
colData(sce2) = DataFrame(sc1@meta.data[keepids,])
sce2

class: SingleCellExperiment 
dim: 30535 17466 
metadata(0):
assays(1): cpm
rownames(30535): ENSMUSG00000108728 ENSMUSG00000094836 ... Csprs
  Vmn1r186
rowData names(0):
colnames(17466): AAACCCAAGGCTCCCA_1_1_1_1 AAACCCAAGTATAGGT_1_1_1_1 ...
  TTTGTTGCACTGAGTT_3_2_2_1 TTTGTTGTCCTCTCGA_3_2_2_1
colData names(30): orig.ident nCount_RNA ... celltype_A1N2
  celltype_N1N2
reducedDimNames(0):
mainExpName: NULL
altExpNames(0):

In [19]:
# get cell type markers on dev data
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$celltype_N1N2)
markers[1:3,]

# save marker list
export_meta_markers(markers, "Govek_celltype_markers_N1N2.csv", names(markers))

group cell_type        gene    fold_change auroc     log_fdr   
1 all   Neurog1_positive Neurog1 17.494133   0.9756427 -339.04653
2 all   Neurog1_positive Rps3     1.272678   0.6204694  -20.70093
3 all   Neurog1_positive Rpl8     1.248728   0.6085722  -16.62490
  population_size population_fraction average_expression se_expression
1 257             0.0147143            208.2525           7.288428    
2 257             0.0147143           1636.7663          53.654575    
3 257             0.0147143           2074.6833          69.034266    
  detection_rate fold_change_detection precision  recall   
1 1.0000000      19.750093             0.23111511 1.0000000
2 0.9805447       1.008068             0.01483138 0.9805447
3 0.9961089       1.001929             0.01474230 0.9961089

In [20]:
head(markers[markers$cell_type=='double_positive',], n = 20)

group cell_type       gene    fold_change auroc     log_fdr   
1  all   double_positive Neurog1 52.492307   0.9921133 -1174.8545
2  all   double_positive Tmsb4x   1.873450   0.8093419  -460.4520
3  all   double_positive Hes6     2.670999   0.8084541  -458.1789
4  all   double_positive Gadd45g  4.051840   0.7989469  -430.2629
5  all   double_positive Npm1     1.789087   0.7831873  -385.6748
6  all   double_positive Mfng     3.467434   0.7813588  -380.8147
7  all   double_positive Btg2     3.457903   0.7776893  -370.9476
8  all   double_positive Rpsa     1.537011   0.7768545  -368.8197
9  all   double_positive Ccnd1    5.320492   0.7685996  -347.0459
10 all   double_positive Rps8     1.490766   0.7684399  -346.7222
11 all   double_positive Rplp1    1.568699   0.7674548  -344.2303
12 all   double_positive Rpl8     1.508921   0.7654045  -339.0465
13 all   double_positive Rps2     1.749681   0.7652374  -338.6825
14 all   double_positive Rpl13    1.492402   0.7635685  -334.5531
15 all   double_positive Rps18    1.674409   0.7631456  -333.5187
16 all   double_positive Rps27a   1.506899   0.7620562  -330.7746
17 all   double_positive Rps4x    1.540550   0.7601586  -325.9816
18 all   double_positive Rps24    1.475598   0.7594815  -324.3092
19 all   double_positive Rps20    1.587408   0.7588926  -322.8620
20 all   double_positive Rps19    1.554780   0.7535556  -309.6589
   population_size population_fraction average_expression se_expression
1  855             0.04895225            220.6233           5.632411   
2  855             0.04895225          10681.0933         172.230528   
3  855             0.04895225            923.8973          21.856356   
4  855             0.04895225            915.1904          35.433023   
5  855             0.04895225           1572.6249          24.859828   
6  855             0.04895225            304.3380           9.357664   
7  855             0.04895225            376.0046          12.594184   
8  855             0.04895225           3079.9949          37.863097   
9  855             0.04895225            561.3869          23.363080   
10 855             0.04895225           3902.4423          43.395071   
11 855             0.04895225           2475.8916          33.824356   
12 855             0.04895225           2455.1762          28.861587   
13 855             0.04895225           1926.5460          33.682542   
14 855             0.04895225           3851.7262          45.254089   
15 855             0.04895225           1945.6059          28.991953   
16 855             0.04895225           2949.4319          34.942806   
17 855             0.04895225           2236.6369          27.909100   
18 855             0.04895225           3356.0480          40.427122   
19 855             0.04895225           2319.2149          32.901088   
20 855             0.04895225           2152.6096          29.455771   
   detection_rate fold_change_detection precision  recall   
1  1.0000000      60.770989             0.76888489 1.0000000
2  1.0000000       1.000662             0.04898310 1.0000000
3  0.9707602       1.362461             0.06555564 0.9707602
4  0.8666667       2.143612             0.09948980 0.8666667
5  0.9964912       1.039833             0.05080501 0.9964912
6  0.8070175       2.775653             0.12524959 0.8070175
7  0.8233918       2.284762             0.10537345 0.8233918
8  1.0000000       1.002109             0.04905054 1.0000000
9  0.7204678       2.834099             0.12758906 0.7204678
10 1.0000000       1.002532             0.04907025 1.0000000
11 1.0000000       1.005868             0.04922563 1.0000000
12 1.0000000       1.006111             0.04923697 1.0000000
13 0.9976608       1.034753             0.05056912 0.9976608
14 1.0000000       1.003258             0.04910407 1.0000000
15 0.9964912       1.040290             0.05082622 0.9964912
16 1.0000000       1.005442             0.04920580 1.0000000
17 1.0000000       1.018000             0.04979036 1.0000000
18 1.00